
# COVID-Team-1
### Dr. Mohanty
### Christopher Brantley
### CSC 405 01
### Last Updated: 11/12/2020
### I, Christopher Brantley, have abided by the UNCG academic policy.

In [1]:
# Changing directory so we can import covid_data.
import os 
os.chdir("../")

## Imports.

In [52]:
import ipynb
from ipynb.fs.full import chris_covid_data as md
from ipynb.fs.full import covid_data as cd
import matplotlib
import matplotlib.pyplot as plt
import numpy as np
import pandas as pd
import plotly.express as px
import plotly.graph_objects as go
import statsmodels.formula.api as smf
import statsmodels.tools.eval_measures as smt

## Pandas Display Options.

In [53]:
# Telling pandas not convert to html tags.
pd.set_option('display.html.table_schema', True)
# Max columns and rows to display.
pd.set_option('display.max_columns', 15)
pd.set_option('display.max_rows', 8)

# Task 1.1: 
# Utilize Linear and Non-Linear (polynomial) regression models to compare trends for a single state and its counties. Start your data from the first day of infections. X-Axis, number of days since the first case, Y-Axis number of new cases and deaths. Calcluate error using RMSE.

In [54]:
df_florida = md.get_state_daily_cases("FL")

In [55]:
def linear_non_models(df_data):
    for poly in range(1, 4):
        pre_formula = "daily_type ~ 1 + days_passed"
        for x in range(2, poly + 1):
            #https://www.statsmodels.org/stable/examples/notebooks/generated/predict.html
            pre_formula  += "+ I(days_passed ** {:.1f})".format(x)
        figure = go.Figure()
        for county in df_data.index:
            series_county = df_data.loc[county]
            first_case_idx = 0
            for value in series_county.values:
                if value != 0:
                    break
                first_case_idx += 1
            x_value = len(series_county[first_case_idx:])
            x_values = np.arange(0, x_value)
            y_values = series_county[first_case_idx:].values
            df_daily_data = pd.DataFrame(columns = ["days_passed", "daily_type"],
                                    data = {"days_passed" : x_values.tolist(),
                                            "daily_type" : y_values.tolist(),
                                           })
            df_x = pd.DataFrame({"days_passed" : df_daily_data.index})
            cur_poly = smf.ols(formula = pre_formula,
                               data = df_daily_data,
                              ).fit()
            pred_y = cur_poly.predict(df_x)
            rmse = smt.rmse(df_daily_data.daily_type.values, pred_y)
            figure.add_trace(go.Scatter(x = df_daily_data.days_passed,
                                        y = pred_y,
                                        mode = "lines",
                                        name = "{} RMSE = {:.2f}".format(county, rmse),
                                       )
                            )
        figure.update_layout(
            title = "Linear and Non-Linear Models Poly n = {}".format(poly),
            xaxis_title = "Days Passed since Initial Case",
            yaxis_title = "Number of Cases",
            legend_title = "Models",
        )
        figure.show()

## Linear/Non-Linear Modeling of New Cases.

In [56]:
linear_non_models(md.get_state_daily_cases("FL"))

## Linear/Non-Linear Modeling of New Deaths.

In [57]:
linear_non_models(md.get_state_daily_deaths("FL"))

#### Linear Model

#### Non-Linear Model

# Task 1.2: 
# Identify which counties are most at risk. Model for top 5 counties with cases within a state and observe their trends.

# Task 1.3: 
# Utilize the hospital data to calculate the point of no return for a state. Use percentage occupancy / utilization to see which states are close and what their trend looks like.

# Task 1.4: 
# Utilize decision tree, random forest, and ARIMA (https://machinelearningmastery.com/arima-for-time-series-forecasting-with-python/) based models to compare and contrast the performance of each. X-variable is the previous weeks data, Y-variable is current week data. So you are predicting one week in advance. Calculate RMSE error. This is just based on number of cases. 

# Task 1.5
# Use 5 different variables from the enrichment data to predict the spread rate (cases and deaths) of COVID-19 in a county. Compare Random Forest and Decision Trees (RMSE error).

## For example, percentage of population in certain age-group, socio-economic status, public transportation, work from home, etc.

## Show the relative importance of variables and explain why. 